<a href="https://colab.research.google.com/github/JohnOx/Capstone_Project_Battle_of_Neighborhoods/blob/main/Best_Place_for_a_Coffee_House_in_Vienna.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<h1>Finding the best place for a Coffee House in Vienna, Austria</h1>

## Applied Data Science Capstone via IBM/Coursera by John Oxales

## Table of contents
* [1. Introduction: Business Problem](#introduction)
* [2. Data](#data)
* [3. Methodology](#methodology)
* [3.1 Analysis](#analysis)
* [4. Results and Discussion](#results)
* [5. Conclusion](#conclusion)


## 1. Introduction: Business Problem<a name="introduction"></a>



#### 1.1 Background
Vienna’s very first coffee house opened in 1683. Even if Vienna was not the pioneer in coffee house culture, it has - over the centuries - established a coffee house tradition like no other city in the world. Coffee and coffee houses are at their best in Vienna!<br>
#### 1.2 Problem
Since so many coffee houses can be already found in any district in Vienna it would be good to know where it would be still reasonable to establish a new coffee house business. It can be assumed that high frequented places like seightseeing spots or malls have already have some coffee houses in vicinity. So an approach would be to find the neighborhood which is still near an area of interest but not overcrowded with or, even better, still lacking a coffee house.<br> 
#### 1.3 Interest
These questions could be of high interest for any new investor or entrepreneur who wants to open one or maybe even more coffee houses in Austria’s capital. This project can also be part of business analytics for larger companies who consider expanding their business. According to the findings, after the following thorough data analysis, those stakeholders can decide where they might open their new coffee house. <br>
For this project I am going to focus on neighborhoods near Vienna's famous historical site: St. Stephen's Cathedral. This place has a very high frequency of tourists and passers-by. 




## 2. Data <a name="data"></a>

#### 2.1 Data sources
The following criteria should be considered to answer the main questions:
- find proper neighborhood candidates near St. Stephen's Cathedral
- distance of those neighborhoods to that area of interest
- number of existing coffee shops in those neighborhoods


The following datasources should be helpful to gain insight and answer the questions:
<br>
##### Datasource:
Foursquare API: "https://developer.foursquare.com/"
##### Purpose: 
Get numbers of coffee houses
##### Datasource: 
Google Maps API reverse geocoding:"https://developers.google.com/maps/documentation/javascript/examples/geocoding-reverse" 
##### Purpose: 
Get centers of candidate areas that will be generated algorithmically and find the approximate addresses of centers of those areas
##### Datasource: 
Google Maps API geocoding:"https://developers.google.com/maps/" 
##### Purpose: 
Get coordinates of St. Stephen's Cathedral and its surrounding


### 2.2 Data acquisition of proper neighborhoods

Starting with obtaining necessary coordinates via Google Maps Geocoding specifically St. Stephen's Cathedral. Latitude and Longitude coordinates of potential neighborhoods are also going to be needed for the centroids. First approach will be to use grid search. So, a layer of grid cells comes into play. 10x10 kilometers centered around St. Stepehen's should do the job in the beginning.

In [ ]:
#@title
google_api_key = 

In [ ]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Stephansdom, Stephansplatz, Wien'
st_stephens = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, st_stephens))

Coordinate of Stephansdom, Stephansplatz, Wien: [48.2084114, 16.3734707]


Next step is to create a grid of area candidates, equaly spaced, centered around St. Stephen's Cathedral and within ~6km from it. Neighborhoods will be defined as circular areas with a radius of 300 meters, so the neighborhood centers will be 600 meters apart.

To accurately calculate distances a grid of locations in Cartesian 2D coordinate system is needed which allows to calculate distances in meters (not in latitude/longitude degrees). Then it will project those coordinates back to latitude/longitude degrees to be shown on Folium map. Further step is to write functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in meters).

In [ ]:
!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

     |████████████████████████████████| 6.6MB 9.2MB/s 


In [ ]:
# Functions to transform geolocation coordinates
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj='utm', zone=19, datum='WGS84') # utm zone of Santiago is 19
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj='utm', zone=19, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('St. Stephens longitude={}, latitude={}'.format(st_stephens[1], st_stephens[0]))

x, y = lonlat_to_xy(st_stephens[1], st_stephens[0])
print('St. Stephens UTM X={}, Y={}'.format(x, y))

lo, la = xy_to_lonlat(x, y)
print('St. Stephens longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
St. Stephens longitude=16.3734707, latitude=48.2084114
St. Stephens UTM X=5610045.163675484, Y=9538774.838646105
St. Stephens longitude=16.373470699999864, latitude=48.208411399999946


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Create a hexagonal grid of cells: offset every other row, and adjust vertical row spacing so that every cell center is equally distant from all it's neighbors.

In [ ]:
st_stephens_x, st_stephens_y = lonlat_to_xy(st_stephens[1], st_stephens[0]) # center location in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = st_stephens_x - 6000
x_step = 600
y_min = st_stephens_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []

for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(st_stephens_x, st_stephens_y, x, y)
        
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.i

364 candidate neighborhood centers generated.


### 2.3 Visualize data on map

In [ ]:
!pip install folium

import folium

Displaying city center location and candidate neighborhood centers:

In [ ]:
map_vienna = folium.Map(location=st_stephens, zoom_start=13)
folium.Marker(st_stephens, popup='St. Stephen\'s Cathedral').add_to(map_vienna)

for lat, lon in zip(latitudes, longitudes):
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_vienna)

map_vienna

Get approximate addresses of those locations with Google Maps API.

In [ ]:
def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        
        return address
    except:
        return None

addr = get_address(google_api_key, st_stephens[0], st_stephens[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(st_stephens[0], st_stephens[1], addr))

Reverse geocoding check
-----------------------
Address of [48.2084114, 16.3734707] is: Stephansplatz 3, 1010 Wien, Austria


In [ ]:
print('Obtaining location addresses: ', end='')
addresses = []

for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    
    if address is None:
        address = 'NO ADDRESS'
        
    address = address.replace(', Austria', '') # We don't need the country part of address
    addresses.append(address)
    print(' .', end='')
    
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [ ]:
addresses[120:150]

['OG1, Währinger Str. 25A, 1090 Wien',
 'Frankhpl. 3, 1090 Wien',
 'Felderstraße 1, 1010 Wien',
 'Schmerlingpl. 6, 1010 Wien',
 'Museumsplatz 1, 1070 Wien',
 'Laimgrubengasse, 1060 Wien',
 'Grüngasse 3, 1050 Wien',
 'Ziegelofengasse 37, 1050 Wien',
 'Stolberggasse 12, 1050 Wien',
 'Geigergasse 7, 1050 Wien',
 'Gudrunstraße 190, 1100 Wien',
 'Fernkorngasse 44, 1100 Wien',
 'Friesenpl. 4, 1100 Wien',
 'Gallmeyergasse 4, 1190 Wien',
 'Gebhardtgasse 13, 1190 Wien',
 'Heiligenstädter Str. 32, 1190 Wien',
 'U-Bahn Bogen 330, 1090 Wien',
 'Institut f. Petrologie d. Universität Wien, Althanstraße 14, 1090 Wien',
 'Julius-Tandler-Platz 2A, 1090 Wien',
 'Porzellangasse 30, 1090 Wien',
 'Berggasse 10, 1090 Wien',
 'Universitätsring 14, 1010 Wien',
 'Minoritenplatz 4, 1010 Wien',
 'Heldenplatz 21/4, 1010 Wien',
 'Gauermanngasse 2-4, 1010 Wien',
 'Schleifmühlgasse 17, 1040 Wien',
 'Rienößlgasse 11, 1040 Wien',
 'Johann-Strauß-Gasse 1, 1040 Wien',
 'Hauslabgasse 5, 1050 Wien',
 'Landgutgasse 61, 110

### 2.4 Create Data Frame out of addresses

In [ ]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address  ...  Distance from center
0         Lienfeldergasse 37, 1160 Wien  ...           5992.495307
1           Thaliastraße 122, 1160 Wien  ...           5840.376700
2           Zagorskigasse 5a, 1160 Wien  ...           5747.173218
3          Possingergasse 15, 1150 Wien  ...           5715.767665
4            Schanzstraße 14, 1150 Wien  ...           5747.173218
5              Märzstraße 99, 1150 Wien  ...           5840.376700
6            Felberstraße 25, 1150 Wien  ...           5992.495307
7  Hernalser Hauptstraße 160, 1170 Wien  ...           5855.766389
8            Effingergasse 6, 1160 Wien  ...           5604.462508
9              Degengasse 17, 1160 Wien  ...           5408.326913

[10 rows x 6 columns]

Save results locally.

In [ ]:
df_locations.to_pickle('./locations.pkl')

### 2.5 Data acquisition of venues via Foursquare API

In [ ]:
#@title


In [ ]:
def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []

    return venues

In [ ]:
# Category IDs corresponding to Coffee Houses were taken from Foursquare web site 
# (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food venues

coffee_categories = ['4bf58dd8d48988d128941735','4bf58dd8d48988d16d941735','4bf58dd8d48988d1e0931735'] #specific roots corresponding to coffee related categories

# filter out needed categories
def is_cafe(categories, specific_filter=None):
    cafe_words = ['café', 'coffee', 'cafeteria', 'coffee shop']
    cafe = False
    specific = False
    
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        
        for r in cafe_words:
            if r in category_name:
                cafe = True
                
        if 'restaurant' in category_name:
            cafe = False
            
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            cafe = True
            
    return cafe, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Austria', '')
    
    
    return address

In [ ]:
import pickle
'''Pickle in Python is primarily used in serializing and deserializing a Python object structure. 
  In other words, it's the process of converting a Python object into a byte stream to store it in a file/database, 
  maintain program state across sessions, or transport data over the network'''

"Pickle in Python is primarily used in serializing and deserializing a Python object structure. \n  In other words, it's the process of converting a Python object into a byte stream to store it in a file/database, \n  maintain program state across sessions, or transport data over the network"

In [ ]:
# Let's now go over our neighborhood locations and get nearby coffee houses; 
# we'll also maintain a dictionary of all other results

def get_cafes(lats, lons):
    cafes = {}
    others = {}
    location_cafes = []

    print('Obtaining venues around candidate locations:', end='')
    
    for lat, lon in zip(lats, lons):
        # Using radius=350 to make sure we have overlaps/full coverage so we don't miss any bar 
        # (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_others = []
        
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            
            is_other, is_cafes = is_cafe(venue_categories, specific_filter=coffee_categories)
            
            if is_other:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                other = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_cafe, x, y)
                
                if (venue_distance<=300):
                    area_others.append(other)
                others[venue_id] = other
                if is_cafes:
                    cafes[venue_id] = other
                    
        location_cafes.append(area_others)
        print(' .', end='')
        
    print(' done.')
    
    return cafes, others, location_cafes

# Try to load from local file system in case of failure
cafes = {}
others = {}
location_cafes = []
loaded = False


# If load failed use the Foursquare API to get the data
if not loaded:
    cafes, others, location_cafes = get_cafes(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('others_350.pkl', 'wb') as f:
        pickle.dump(others, f)
    with open('cafes_350.pkl', 'wb') as f:
        pickle.dump(cafes, f)
    with open('location_cafes_350.pkl', 'wb') as f:
        pickle.dump(location_cafes, f)

Obtaining venues around candidate locations:

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


 .

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


 . . .

...

 . . .

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


 . . . . . . . . . .

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


 . . done.


Display results

In [ ]:
import numpy as np

print('Total number of Others:', len(others))
print('Total number of Coffee Houses:', len(cafes))

print('Average number of cafes in neighborhood:', np.array([len(r) for r in location_cafes]).mean())

Total number of Others: 353
Total number of Coffee Houses: 353
Average number of cafes in neighborhood: 1.2912087912087913


In [ ]:
print('List of all Cafes')
print('-----------------------')

for r in list(cafes.values())[:10]:
    print(r)
    
print('...')
print('Total:', len(cafes))

List of all Cafes
-----------------------
('4fcbd1aee4b035b338509316', 'Saadi', 48.213484148533716, 16.313546831840526, 'Wien, Österreich', 168, <function is_cafe at 0x7f0090b33d40>, 5608651.775022463, 9532943.225227607)
('4dbaa0fb5da389d2c23f4a17', 'Cafe Raiman', 48.212493540644395, 16.313426540201228, 'Thaliastraße 134 (Lienfeldergasse), 1160 Wien, Österreich', 113, <function is_cafe at 0x7f0090b33d40>, 5608796.704445444, 9532915.317294477)
('590ed01b0a464d19efde908a', 'Cafe Mesk', 48.198006, 16.318914, 'Johnstrasse 57 (Meiselstrasse), Wien, Österreich', 268, <function is_cafe at 0x7f0090b33d40>, 5610994.963839473, 9533222.365220863)
('505f1567e4b0a0608506cd78', 'Joules Bistro', 48.19073776714951, 16.318095670578284, 'Mariahilfer Straße 212, 1140 Wien, Österreich', 162, <function is_cafe at 0x7f0090b33d40>, 5612059.346630425, 9533023.946083631)
('4ea501c5e3008f7d9327cde7', 'Cafe Jessy', 48.193207, 16.313825, 'Wien, Österreich', 344, <function is_cafe at 0x7f0090b33d40>, 5611648.48509

In [ ]:
print('Cafes around location')
print('---------------------------')

for i in range(100, 110):
    rs = location_cafes[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Cafess around location {}: {}'.format(i+1, names))

Cafes around location
---------------------------
Cafess around location 101: Cafe Schopenhauer, Café Weimar, Café Oper, Coffeeshop Company WIFI Wien 1. Stock
Cafess around location 102: Caffe Milano, Café Weimar
Cafess around location 103: The Pelican Coffee Company, Aida Café-Konditorei Wien, Eduscho Alserstrasse
Cafess around location 104: Hildebrandt Café, Cafe der Provinz, Café Merkur, Café Maria Treu, Café Nöbauer, Alser Cafe
Cafess around location 105: Café Strozzi, Café Maria Treu
Cafess around location 106: Erich, Café in der Burggasse, Espresso, Alte Bäckerei, Kulturzentrum & Café 7*Stern, das möbel, Café Comet
Cafess around location 107: My Secret Garden, Kulturzentrum & Café 7*Stern, Konditorei Blocher, Liebling, Figar, Café Kafka, Cafe im Raimundhof, Café Nil
Cafess around location 108: ocean’sky & hammerhai, Rüdigerhof, Schadekgasse12
Cafess around location 109: Rüdigerhof, Cafe Maestro
Cafess around location 110: 


### 2.6 Visualize Results on Map

Looking at collected coffee houses in area of interest

In [ ]:
map_vienna = folium.Map(location=st_stephens, zoom_start=13)
folium.Marker(st_stephens, popup='St. Stephen\s Cathedral').add_to(map_vienna)

for res in cafes.values():
    lat = res[2]; lon = res[3]
    is_cafe = res[6]
    color = 'red' if is_cafe else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_vienna)
    
map_vienna

The map displays all found coffee houses near St. Stephen's Cathedral within a radius of 10 kilometers. Furthermore, which coffee house is in vicinity of every potential neighborhood candidate.

With this gathered information a thorough data analysis will be the next step.

## 3. Methodology <a name="methodology"></a>

In order to find those promising neighborhoods with a low density of coffee houses (or no coffee shops at all) a heatmap in the beginning is going to be the tool of choice. To keep it simple the area of inspection will be limited within ~6km around St. Stephen's.

Next step will include the use of clusters i.e. k-means clustering which will be visualized on a map.

### 3.1 Analysis <a name="analysis"></a>

Starting exploratory analysis with counting coffee houses in every area candidate:

In [ ]:
location_cafes_count = [len(cafe) for cafe in location_cafes]
df_locations['Cafes in area'] = location_cafes_count

print('Average number of Cafes in every area with radius=300m:', np.array(location_cafes_count).mean())

df_locations.head(10)

Average number of Cafes in every area with radius=300m: 1.2912087912087913


Address  ...  Cafes in area
0         Lienfeldergasse 37, 1160 Wien  ...              0
1           Thaliastraße 122, 1160 Wien  ...              2
2           Zagorskigasse 5a, 1160 Wien  ...              0
3          Possingergasse 15, 1150 Wien  ...              0
4            Schanzstraße 14, 1150 Wien  ...              1
5              Märzstraße 99, 1150 Wien  ...              1
6            Felberstraße 25, 1150 Wien  ...              1
7  Hernalser Hauptstraße 160, 1170 Wien  ...              1
8            Effingergasse 6, 1160 Wien  ...              0
9              Degengasse 17, 1160 Wien  ...              1

[10 rows x 7 columns]

Calculate the distance to nearest Coffee House from every area candidate center (not only those within 300m - especially the distance to the closest one, regardless of how distant it is).

In [ ]:
distances_to_cafe = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    
    for res in cafes.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        
        if d<min_distance:
            min_distance = d
            
    distances_to_cafe.append(min_distance)

df_locations['Distance to Coffee House'] = distances_to_cafe

In [ ]:
df_locations.head(10)

Address  ...  Distance to Coffee House
0         Lienfeldergasse 37, 1160 Wien  ...                422.791942
1           Thaliastraße 122, 1160 Wien  ...                151.701745
2           Zagorskigasse 5a, 1160 Wien  ...                664.202150
3          Possingergasse 15, 1150 Wien  ...                707.645372
4            Schanzstraße 14, 1150 Wien  ...                386.037775
5              Märzstraße 99, 1150 Wien  ...                298.772433
6            Felberstraße 25, 1150 Wien  ...                217.043997
7  Hernalser Hauptstraße 160, 1170 Wien  ...                 54.630640
8            Effingergasse 6, 1160 Wien  ...                609.972800
9              Degengasse 17, 1160 Wien  ...                180.687513

[10 rows x 8 columns]

In [ ]:
print('Average distance to closest Coffee House from each area center:', df_locations['Distance to Coffee House'].mean())


Average distance to closest Coffee House from each area center: 403.2494863780251


On average the next coffee house can be found within ~400m from every area center candidate.
Next step will be to show those results i.e. the density on a heatmap.

In [ ]:
cafes_latlons = [[cafe[2], cafe[3]] for cafe in cafes.values()]

In [ ]:
from folium import plugins
from folium.plugins import HeatMap

In [ ]:
map_vienna = folium.Map(location=st_stephens, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_vienna) #cartodbpositron cartodbdark_matter
HeatMap(cafes_latlons).add_to(map_vienna)
folium.Marker(st_stephens).add_to(map_vienna)
folium.Circle(st_stephens, radius=1000, fill=False, color='white').add_to(map_vienna) # 1km indicator
folium.Circle(st_stephens, radius=2000, fill=False, color='white').add_to(map_vienna) # 2km indicator
folium.Circle(st_stephens, radius=3000, fill=False, color='white').add_to(map_vienna) # 3km indicator

map_vienna

###3.2 Heatmap interpretation
It seems obvious that around St. Stephen's is a high density of coffee houses. This is not surprising since it is in the heart of Vienna and many other historical sites and shopping possibilities can be found there. Also within 1km, which can be defined as Vienna's downtown, shows some significance in coffee houses density. <br> 

So, shifting focus to another promising area within 3km range would be interesting. My personal decision will be the neighborhood called 'Stuwerviertel'. It is located about 2,5km north-eastern from St. Stephen's. It is a high emerging, modern area with a lot of newly built office complexes, apartments and the University for Business and Economics is also very near. Not forgetting to mention its close range to Vienna's famous theme park 'Praters'. All in all a very promising spot with potential coffee consuming customers and very low density of coffee houses.

### 3.3 Focus: 'Stuwerviertel'

In [ ]:
# shifting coordinates to Stuwerviertel 2,5km north-east from current position
# calculating new position
roi_x_min = st_stephens_x - 3000
roi_y_max = st_stephens_y + 5000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_vienna = folium.Map(location=roi_center, zoom_start=14)
HeatMap(cafes_latlons).add_to(map_vienna)
folium.Marker(st_stephens).add_to(map_vienna)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_vienna)

map_vienna

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Create a more narrow grid for 'Stuwerviertel' to find potential spots

In [ ]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyp

2261 candidate neighborhood centers generated.


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()


Calculate distances(radius=250 meters) to closest coffee shops in vicinity

In [ ]:
def count_cafes_nearby(x, y, cafes, radius=250):    
    count = 0
    
    for cafe in cafes.values():
        cafe_x = cafe[7]; cafe_y = cafe[8]
        d = calc_xy_distance(x, y, cafe_x, cafe_y)
        if d<=radius:
            count += 1
            
    return count

def find_nearest_cafe(x, y, cafes):
    d_min = 100000
    
    for cafe in cafes.values():
        cafe_x = cafe[7]; cafe_y = cafe[8]
        d = calc_xy_distance(x, y, cafe_x, cafe_y)
        
        if d<=d_min:
            d_min = d
            
    return d_min

roi_cafe_counts = []
roi_cafe_distances = []

print('Generating data on location candidates... ', end='')

for x, y in zip(roi_xs, roi_ys):
    
    count = count_cafes_nearby(x, y, cafes, radius=250)
    roi_cafe_counts.append(count)
    distance = find_nearest_cafe(x, y, cafes)
    roi_cafe_distances.append(distance)
print('done.')


Generating data on location candidates... done.


Create Data Frame

In [ ]:
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Cafes nearby':roi_cafe_counts,
                                 'Distance to Cafes (in meters)':roi_cafe_distances})

df_roi_locations.head(10)

Latitude  Longitude  ...  Cafes nearby  Distance to Cafes (in meters)
0  48.212093  16.372874  ...             3                     111.666245
1  48.211424  16.372983  ...             5                      66.080883
2  48.215838  16.373145  ...             0                     445.677344
3  48.215168  16.373254  ...             0                     347.725346
4  48.214499  16.373362  ...             0                     251.391203
5  48.213829  16.373470  ...             1                     159.631319
6  48.213160  16.373579  ...             1                      88.129331
7  48.212491  16.373687  ...             2                     100.256670
8  48.211821  16.373796  ...             5                     159.231838
9  48.211152  16.373904  ...             4                      84.495210

[10 rows x 6 columns]

Sorting out locations with no more than two coffee houses within a range of 250 meters:

In [ ]:
good_cafe_count = np.array((df_roi_locations['Cafes nearby']<=2))
print('Locations with no more than two Cafes nearby:', good_cafe_count.sum())

good_cafe_distance = np.array(df_roi_locations['Distance to Cafes (in meters)']<=250)
print('Locations with no Cafes within 250m:', good_cafe_distance.sum())

good_locations = np.logical_and(good_cafe_count, good_cafe_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two Cafes nearby: 2075
Locations with no Cafes within 250m: 889
Locations with both conditions met: 703


### 3.4 Visualize final results on map

In [ ]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_vienna = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_vienna)
HeatMap(cafes_latlons).add_to(map_vienna)
folium.Circle(roi_center, radius=1500, color='white', fill=True, fill_opacity=0.6).add_to(map_vienna)
folium.Marker(st_stephens).add_to(map_vienna)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_vienna) 

map_vienna

### 3.5 Map interpretation
All blue markers show potential locations for a new coffee house. They meet the specified parameters: 
- no more than 2 coffee houses
- within 250m <br>

The following heatmap will clarify those results:

In [ ]:
map_vienna = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_vienna)
folium.Marker(st_stephens).add_to(map_vienna)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_vienna)

map_vienna

### 3.6 Cluster Results
With the use of a clustering method those promising areas are going to be stressed out a bit more. After defining those zones, their centers and addresses this should lead to the final result of the analysis.

In [ ]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_vienna = folium.Map(location=roi_center, zoom_start=15)
folium.TileLayer('cartodbpositron').add_to(map_vienna)
HeatMap(cafes_latlons).add_to(map_vienna)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_vienna)
folium.Marker(st_stephens).add_to(map_vienna)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_vienna) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_vienna)

map_vienna

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyp

### 3.7 Cluster Interpretation
The clusters (green circles) represent groupings of the most promising locations.

Addresses of those cluster centers will be a good starting point for further exploration in those neighborhoods based on specified requirements.

Visualize Clusters without Heatmap

In [44]:
map_vienna = folium.Map(location=roi_center, zoom_start=14)

folium.Marker(st_stephens).add_to(map_vienna)

for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_vienna)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_vienna)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_vienna) 

map_vienna

### 3.8 Reverse Geocoding

In [45]:
# script to reverse coordinates into readable addresses using reverse geocoding

candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', Austria', '')
    

    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, st_stephens_x, st_stephens_y)
    print('{}{} => {:.1f}km from St. Stephen\'s Cathedral'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


Hintzerstraße 9, 1030 Wien                         => 2.1km from St. Stephen's Cathedral


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


Praterstraße 58, 1020 Wien                         => 1.8km from St. Stephen's Cathedral


...

Postgasse 16, 1010 Wien                            => 0.7km from St. Stephen's Cathedral


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


Engerthstr. 232-238, 1020 Wien                     => 4.5km from St. Stephen's Cathedral
Löwenherzgasse 10, 1030 Wien                       => 2.9km from St. Stephen's Cathedral


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  """


Gärtnergasse 10, 1030 Wien                         => 1.5km from St. Stephen's Cathedral
Donaukanal Str. 60, 1030 Wien                      => 2.3km from St. Stephen's Cathedral


### 3.9 End of Analysis

This concludes the analysis. 15 addresses representing centers of zones containing locations with low number of Coffee Houses nearby, all zones being fairly close to St. Stephen's Cathedral (all less than 5km from this location). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential coffee house locations. Most of the zones are located in 'Stuwerviertel' borough, which is identified to be interesting due to being popular with tourists, fairly close to St. Stephen's and well connected by public transport.

In [46]:
map_vienna = folium.Map(location=roi_center, zoom_start=15)
folium.Circle(st_stephens, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_vienna)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_vienna)
    
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_vienna)
    
map_vienna

## 4. Results and Discussion <a name="results"></a>

Summarizing all the findings it led to focus on a new area of interest which is 'Stuwerviertel' and its surroundings. Started at Vienna's most centered and important historical site, St. Stephen's Cathedral to locate areas with high densities of coffee shops which could be excluded and identify spots with low density. One of those zones was finally 'Stuwerviertel'. After calculating specified distances and finding nearby coffee houses it still met defined requirements. With the help of clustering potential zones and addresses could be obtained. 

## 5. Conclusion <a name="conclusion"></a>

It should be mentioned that there are other potential candidates areas. Shifting focus to that specific region 'Stuwerviertel' was a personal decision based on current observations and knowledge. A lot factors speaks for the attractiveness of that upcoming and trendy area which offers a lot of business possibilities in the end. For a more accurate analysis of course, different key indicators would have to be taken in consideration like rent-prices, available rent objects, tourist-frequency, number of offices and so on. This project delievers a first overview of potential locations to offer initial recommendations for the stakeholders. 